In [1]:

import warnings
import numpy as np
import pandas as pd
import matplotlib
import matplotlib.pyplot as plt

from PIL import Image
# suppress warnings
import matplotlib.image as mpimg
warnings.filterwarnings ( 'ignore' )
%matplotlib inline
import os 

import re
import time



import cartopy.crs as ccrs
import cartopy.feature as cfeature
import matplotlib.pyplot as plt
import cartopy.io.shapereader as shpreader
from cartopy.io.shapereader import Reader
from cartopy.feature import ShapelyFeature

from matplotlib.dates import MO, TU, WE, TH, FR, SA, SU

import datetime

%matplotlib inline
pd.set_option("max_columns", None)

import mplleaflet

import geopandas as gpd

import shapely

import seaborn as sns

import pysal as ps

from geopandas import GeoDataFrame
from shapely.geometry import Point



In [29]:
%%html
<style>
div.input {
    display:none;
}
</style>

In [2]:
car = gpd.read_file("data-2/outputs/mv_massdot_clusters_top_quartile.shp")

bike = gpd.read_file("data-2/outputs/bk_massdot_clusters_top_quartile.shp")

person = gpd.read_file("data-2/outputs/pd_massdot_clusters_top_quartile.shp")



In [3]:
schools = gpd.read_file("Public_Schools/Public_Schools.shp")


In [4]:
bike = bike.to_crs({'init': 'epsg:4326'}) #unit=degree
car = car.to_crs({'init': 'epsg:4326'})
person = person.to_crs({'init': 'epsg:4326'}) 

schools = schools.to_crs({'init': 'epsg:4326'})



In [5]:
df1 = pd.read_csv("../postjun14tojun16over55MPH.csv")  #cleaned speed data for june 2014 to june 2016 with lat/lon and timestamp


In [6]:
b = df1.sort(['study_id','Neighborhood Code','timestamp'],ascending=[1,1,0])



In [7]:
top5 = b.groupby(['study_id', 'Neighborhood Code']).head(1)


In [8]:
#to geopandas for df with lat lon
geometry = [Point(xy) for xy in zip(top5.lon, top5.lat)]
top5 = top5.drop(['lon', 'lat'], axis=1)
crs = {'init': 'epsg:4326'}
speedPostJun2014toJun2016Over55 = GeoDataFrame(top5, crs=crs, geometry=geometry)

In [9]:
schools = schools[["SCH_TYPE","geometry"]]


In [10]:
highSchools = schools[schools["SCH_TYPE"] == "HS"]
elementarySchools = schools[schools["SCH_TYPE"] == "ES"]

In [11]:
fatalbike = bike[bike["fatal"] > 0]
fatalcar = car[car["fatal"] > 0]
fatalperson = person[person["fatal"] > 0]


In [12]:
b = bike.injury.mean()*2
c = car.injury.mean()*2
p = person.injury.mean()*2
#print(b, c, p)

In [13]:
#scores that are greater than twice the average score 
bikehighscore = bike[bike["score"] > bike.score.mean()*2 ]

carhighscore = car[car["score"] > car.score.mean()*2]
personhighscore = person[person["score"] > person.score.mean()*2]




In [14]:
##google API lat lon of sign locations using CofB list, 28 existing signs

myData = [
[42.2881149,-71.0765092, '114 Norfolk St, Boston, MA 02124, USA'],
[42.3488745,-71.047996, '349 Summer St, Boston, MA 02210, USA'],
[42.3535392,-71.0805744, '266 Beacon St, Boston, MA 02116, USA'],
[42.4043409,-71.1146198, '540 Boston Ave, Medford, MA 02155, USA'],
[42.3747976,-71.06268, '26 Pleasant St, Charlestown, MA 02129, USA'],
[42.3293958,-71.0859364, '56 Malcolm X Blvd, Boston, MA 02119, USA'],
[42.2759765,-71.1391773, '4594 Washington St, Roslindale, MA 02131, USA'],
[42.368105,-71.0553854, '513 Commercial Street, Boston, MA 02109, USA'],
[42.3792242,-71.0627021, '215 Bunker Hill St, Boston, MA 02129, USA'],
[42.2896589,-71.0655406, '112 Welles Ave, Dorchester Center, MA 02124, USA'],
[42.2738241,-71.1156024, '980 American Legion Hwy, Roslindale, MA 02131, USA'],
[42.3527483,-71.1545233, '76 Parsons St, Brighton, MA 02135, USA'],
[42.3536654,-71.1547646, '104 Parsons St, Brighton, MA 02135, USA'],
[42.3091289,-71.0992832, 'Sigourney St, Boston, MA 02130, USA'],
[42.3093904,-71.0992152, '32 Sigourney St, Jamaica Plain, MA 02130, USA'],
[42.2576767,-71.1564091, '351 Grove St, West Roxbury, MA 02132, USA'],
[42.2592392,-71.1569306, '297 Grove St, West Roxbury, MA 02132, USA'],
[42.2759916,-71.1478839, '125 Lagrange St, Boston, MA 02132, USA'],
[42.2756907,-71.1485453, '148 Lagrange St, West Roxbury, MA 02132, USA'],
[42.231264,-71.06957, '27 Hilltop St, Milton, MA 02186, USA'],
[42.2316041,-71.0686892, '44 Hilltop St, Milton, MA 02186, USA'],
[42.3818667,-71.0210452, '504 Bennington St, Boston, MA 02128, USA'],
[42.385073,-71.012298, '720 Bennington St, Boston, MA 02128, USA'],
[42.3825924,-71.0360732, 'Condor St & Brooks St, Boston, MA 02128, USA'],
[42.3825711,-71.0302649, 'Condor St & Glendon St, Boston, MA 02128, USA'],
[42.2898668,-71.1182296, 'Hyde Park Ave & Southbourne Rd, Boston, MA 02131, USA'],
[42.3863301,-71.0058148, 'MA-145 & Bayswater St, Boston, MA 02128, USA'],
[42.2889812,-71.0527708, 'Ashmont St & Humes Rd, Boston, MA 02122, USA']
];

In [15]:
lat = myData[0][0]
lon = myData[0][1]

i=0
lat1 = []
for thing in myData:
    lat = myData[i][0]
    lat1.append(lat)
    i = i+1
    
x=0
long1 = []
for thingX in myData:
    long = myData[x][1]
    long1.append(long)
    x = x+1



In [16]:
d = {'lat': pd.Series(lat1),'lon' : pd.Series(long1)}



In [17]:
df = pd.DataFrame(d)


In [18]:
geometry = [Point(xy) for xy in zip(df.lon, df.lat)]
df = df.drop(['lon', 'lat'], axis=1)
crs = {'init': 'epsg:4326'}
signs_geodf = GeoDataFrame(df, crs=crs, geometry=geometry)


In [19]:
bnetwork = gpd.read_file("Existing_Bike_Network/Existing_Bike_Network.shp")
bnetwork = bnetwork.to_crs({'init': 'epsg:4326'})

In [20]:
#car and pedestrian has more fatalities so will look at that below with the signs
#print(len(car[car["fatal"] > 0]),len(bike[bike["fatal"] > 0]),len(person[person["fatal"] > 0]))

## Car passengers and pedestrians suffer the most fatalities, according to city data. The map shows areas with car, pedestrian and biking deaths in blue, red and green, respectively. The blue lines indicate the bike network.

In [21]:
f = plt.figure(figsize=(15, 8))
ax = f.gca()
fatalcar.plot(ax=ax, color='b',markersize=10)#fatals are there but very small in leaflet and hard to see without zoom
fatalbike.plot(ax=ax, color='r',)
fatalperson.plot(ax=ax, color='g',)
bnetwork.plot(ax=ax, color='c')
mplleaflet.display(fig=f)



## Accidents with fatalities or more injuries receive a higher score in the crash data.  The map shows incidents with scores that are at least twice the average for the data. They're clearly busy areas for all types of traffic. Many are near schools, which are marked with magenta dots. 

In [22]:
f = plt.figure(figsize=(15, 8))
ax = f.gca()

#signs_geodf.plot(ax=ax, color='tab:orange', markersize=5) #they are super tiny without marker size
#speedPostJun2014toJun2016Over55.plot(ax=ax, color='tab:brown', markersize=5,)


#at least twice the average score
carhighscore.plot(ax=ax, color='b', )#fatals are there but very small in leaflet and hard to see without zoom

bikehighscore.plot(ax=ax, color='r',)

personhighscore.plot(ax=ax, color='g',)

bnetwork.plot(ax=ax, color='c')

highSchools.plot(ax=ax, color='m', markersize=5,alpha=0.8)
elementarySchools.plot(ax=ax, color='m', markersize=5, alpha=0.8)



mplleaflet.display(fig=f)




In [23]:
highscore_bike_plus_person = gpd.overlay(personhighscore, bikehighscore, how='intersection')

In [24]:
highscore_car_plus_person = gpd.overlay(personhighscore, carhighscore, how='intersection')

## Areas where these accidents intersect might make good candidates for more signs. The red areas show where high-scoring car and pedestrian accidents overlap. They are fairly compact areas so you have to zoom to find them. 

In [28]:
f = plt.figure(figsize=(15, 8))
ax = f.gca()



#signs_geodf.plot(ax=ax, color='tab:orange', markersize=5, alpha=0.5) #they are super tiny without marker size
#speedPostJun2014toJun2016Over55.plot(ax=ax, color='g', markersize=10,alpha=0.5)

#bikehighscore.plot(ax=ax, color='b', markersize=10,)#fatals are there but very small in leaflet and hard to see without zoom

highscore_car_plus_person.plot(ax=ax, color='r',markersize=5, alpha=1)


bnetwork.plot(ax=ax, color='c',)

highSchools.plot(ax=ax, color='m', markersize=5, alpha=0.8)
elementarySchools.plot(ax=ax, color='m', markersize=5, alpha=0.8)



mplleaflet.display(fig=f)



## The reddish areas show overlap between high-scoring bike and pedestrian accident sites. High-scoring car incidents are still in blue and some of them overlap. The red dots are roughly the location of existing signs. Many of these areas are busy intersections and some are already the focus of city efforts. That said, a useful step would be to map the rate of accidents based on the amount of car, bike and pedestrian traffic to really pinpoint the most dangerous areas. Thanks! -- Heather Walsh

In [25]:
f = plt.figure(figsize=(15, 8))
ax = f.gca()



signs_geodf.plot(ax=ax, color='r', markersize=5, alpha=0.9) #they are super tiny without marker size

#speedPostJun2014toJun2016Over55.plot(ax=ax, color='r', markersize=5,alpha=0.9)


carhighscore.plot(ax=ax, color='b', alpha=0.9)#fatals are there but very small in leaflet and hard to see without zoom

highscore_bike_plus_person.plot(ax=ax, color='r',markersize=5, alpha=0.9)


bnetwork.plot(ax=ax, color='c')

highSchools.plot(ax=ax, color='m', markersize=5, alpha=0.8)
elementarySchools.plot(ax=ax, color='m', markersize=5, alpha=0.8)



mplleaflet.display(fig=f)